In [1]:
import pandas as pd
import numpy as np
import numba as nb
import requests
import regex as re
import time
import gc
import copy
import json
from statistics import mean

from numba import jit, cuda, prange, typeof, typed, types
from numpy.linalg import norm

from multiprocessing import Pool, Manager

# ignore warnings (gets rid of Pandas copy warnings)
import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = None

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)

#from scipy import sparse
#from scipy.sparse import csr_matrix
#from scipy import spatial

#from sklearn.metrics.pairwise import cosine_similarity
#import sklearn.preprocessing as pp
#from sklearn.preprocessing import StandardScaler, PolynomialFeatures, MinMaxScaler, OneHotEncoder
from sklearn.preprocessing import MinMaxScaler, normalize

import tensorflow as tf
from tensorflow.compat.v1.losses import cosine_distance
from tensorflow.keras.losses import CosineSimilarity

In [3]:
# the basic file required for this work - the full matrix

larger_matrix = pd.read_pickle('real_ratings/users_real_scaled_fullmatrix.pkl')

In [4]:
gameids_columnorder = list(larger_matrix.columns)
gameids_columnorder[:10]

['213788',
 '206593',
 '267333',
 '249824',
 '301085',
 '261321',
 '264212',
 '249552',
 '290618',
 '302933']

In [5]:
del larger_matrix
gc.collect()

22

In [6]:
# Opening JSON file
with open('item_similarities_raw/item_similarity_storage_real.json') as json_file:
    item_similarities = json.load(json_file)

In [7]:
# Opening JSON file
with open('item_similarities_raw/item_similarity_storage_250synthetic.json') as json_file:
    item_similarities = json.load(json_file)

In [8]:
cleaned_storage = {}

for each_list in item_similarities:
    
    for item in each_list:
        
        print(item)
        cleaned_storage[item] = {}
        
        for i in np.arange(21925):
            
            similarity = each_list[item][i]
            
            if similarity == 1.0:
                continue
            #elif similarity == 0.0:
            #    continue
            elif similarity >= 0.75:
                similar_item = gameids_columnorder[i]
                cleaned_storage[item][similar_item] = similarity

213788
206593
267333
249824
301085
261321
264212
249552
290618
302933
303734
302510
281094
280281
271064
240096
239808
232944
231309
227212
192696
319999
304434
232250
226085
230885
286885
290722
287839
317313
240423
252323
209667
241203
328569
248695
266079
272767
274152
258775
312613
311751
261588
261246
36218
133473
167791
230802
174430
70919
40834
463
181304
163412
170216
199561
70323
155426
147020
266192
160477
100423
205896
10547
9220
172287
198994
291457
161936
233867
265736
176396
65244
147949
43443
2653
199792
269207
221965
172818
218603
174660
283155
150312
123540
221194
195421
155987
271896
22141
69789
171233
45
296151
112686
298047
256382
281259
197376
295947
160851
12692
199042
232219
297030
201825
258036
16992
217449
184921
244536
240196
192153
131835
197831
264055
123506
169555
154174
204472
108784
328871
207243
284378
168609
247236
147253
91620
304285
227758
117942
193737
252153
248158
95064
205046
291508
185589
244191
228660
239472
192074
271518
205322
222514
284742
14

121408
7717
245476
2093
714
270844
244228
274637
88408
554
12902
394
176165
218121
250458
274960
986
304420
117985
201
283393
171908
230914
199966
264241
270314
274638
303057
294484
442
1915
200057
127997
258444
216600
256570
251219
244049
267319
153
314491
128554
89952
191597
301716
285265
269752
284777
76150
257066
291794
139993
3495
296100
127127
17419
222219
277699
325635
274466
266966
252752
251551
142555
266965
266967
11104
266964
271529
152510
245200
238799
1586
22766
2139
275974
155460
294230
5709
270143
12237
179228
6686
158316
80833
205158
9209
97786
121288
279254
168421
160744
220
281075
266507
298069
207991
146886
186375
25417
229491
55834
280480
19947
258140
173047
249889
46
298383
128063
269210
217099
301946
298130
4529
114863
256874
30241
9200
329465
156113
180592
117914
310192
245325
219475
129820
141102
248005
1621
40793
3656
180471
126
237079
199881
63433
284949
143782
179172
118703
258154
29146
5336
260180
133671
28050
295564
113927
12962
4330
224783
257378
162114
19

163565
20036
127561
173755
264141
331573
256065
38944
302260
414
229537
34829
27833
183197
2532
205667
237145
41529
297895
161886
185262
329641
128028
91050
202723
5209
289427
174696
104063
156
256297
140675
282954
15159
267036
141681
1207
182978
254494
141572
119012
176523
172550
256390
100473
225910
197409
209283
218574
263177
98778
6249
31481
5
39463
124742
161970
157969
43570
29368
41
12942
34219
155362
27225
77130
170416
137297
101721
17329
2394
11170
37111
21050
194607
21882
20100
206718
108745
25292
152162
104363
503
170
19100
177590
915
1382
30539
131646
17053
32125
54137
39339
9609
174785
245643
91312
13004
154386
12333
107529
16747
38159
21523
128996
256
36235
17223
249259
18833
38453
43111
115746
59294
174688
168174
101785
1042
172931
619
106
31999
66171
57390
35052
284760
398
247367
73171
24800
1275
254386
3181
319966
255674
27976
29294
206940
182189
140519
9028
63543
183231
191004
4209
169
125311
19643
1107
71061
258210
204516
132028
67492
147154
135219
833
276830
92044
18

39351
121297
43528
179572
70512
161614
175324
200077
40765
233247
104710
124
103886
119
91
19777
27746
55670
145659
2346
26990
154809
157403
62227
65515
242639
95527
180511
154458
815
2955
187617
171669
206941
181521
140603
134253
191231
42452
204305
131287
146791
30645
528
3685
117915
144344
157809
144592
35815
95103
37628
162286
72225
130176
3699
129948
42487
119591
169255
192836
134453
119432
71671
138788
45358
183880
27708
176734
2165
143515
146278
193558
188920
5894
119506
195314
145639
72321
106217
226320
41916
2375
194880
198454
113066
125547
125549
126206
127258
129086
173899
176306
176872
181245
183750
183401
166156
166246
40559
38050
38197
29142
28511
66641
142992
156943
105037
111341
715
144797
163839
116954
4174
108906
157789
111124
34297
34194
129051
135382
466
55427
33451
154086
82421
527
160495
6830
172381
12761
13884
111417
38862
82420
230933
13780
75449
43022
214032
148203
194690
217780
159503
65907
92190
39684
8190
103185
192860
908
23094
23686
176
143185
69552
92319


8195
23540
155731
159492
40831
20750
281946
229218
71655
253608
169147
304783
171129
138649
131891
206175
163640
142121
209660
140865
227545
180867
182218
38364
31545
125315
307002
130911
148291
217776
189294
177939
144568
141090
284429
303954
57052
202755
144525
147194
123228
171110
25695
236304
236781
218376
141735
187353
173294
291453
191579
175458
183572
182770
144468
176816
32424
4421
163929
200783
196217
127994
155822
155322
245446
203716
151251
145599
150539
185378
185380
185381
191065
235767
245952
244951
319031
340834
337262
14538
85256
44163
28
27364
113401
131325
5432
99975
231733
290236
213266
20545
281442
220517
198953
298065
202426
196526
128664
204505
22484
270836
255668
253635
302524
145588
248900
318553
312251
130792
302520
19427
89415
182704
3341
279869
115233
309110
280032
5770
285894
280132
32944
316622
267009
204837
159581
329839
275469
234828
159566
330038
220203
302344
257056
219512
207910
252265
220778
282439
197072
255594
299372
158882
282493
13597
227605
23185

...

24826
24189
25469
25760
25312
25097
25158
25188
25270
30723
30281
29694
27584
27668
27712
28674
29018
41190
91442
91653
92591
92879
93044
91440
89915
90004
90016
90471
79413
86025
84989
41310
100758
105434
104775
104798
93997
94116
99166
98371
99707
49454
58139
42188
41958
69205
69275
72957
65488
67144
67429
9408
67593
1218
21930
2872
40935
64
66613
234877
4401
4493
1379
20082
74102
82402
65568
756
210
24771
105199
366
482
32405
1416
27306
34701
2833
136284
21022
129615
93688
18750
5711
387
3119
4522
335
304
476
67
1510
34284
35812
27363
317
280203
343
428
117555
429
7483
416
459
30239
29411
28436
1352
2366
108705
118215
113
574
13089
109
9354
171620
120305
235944
449
440
29020
314
332
33071
1970
227693
6368
6187
131493
45319
218957
303
89403
211
993
13436
820
127436
206925
2740
137480
136416
134626
91512
1087
180
89972
183
85338
906
910
900
144223
1007
144
193161
605
558
711
136058
136415
207
88464
202296
1803
32702
424
266802
8939
24977
23421
7526
6949
187186
202227
13488
8533
42006


23818
14471
14474
17939
3129
3122
3042
2440
2442
2403
2380
2550
3848
3884
3270
3486
3598
3502
957
844
1208
762
648
1443
1750
1819
1857
7802
7579
7823
7203
7102
5054
4494
4508
5786
5961
5338
5347
149611
151947
145587
146104
122961
123915
121324
114386
115944
124991
127229
127317
176466
175845
168840
181263
183212
179629
160420
158495
158589
165578
162677
36237
36238
37477
38868
24079
25001
25299
30246
31360
29278
89926
89928
80474
84776
102159
101628
93867
96608
98189
56195
50764
42660
41844
42748
47410
72373
74678
75292
75587
290484
17484
17393
200551
911
1678
18485
7104
123129
28907
251747
244170
7182
54372
14134
33924
244171
242227
3466
1447
96026
183578
62230
188390
23685
3177
22359
142889
226089
2192
137336
157323
250481
289
937
72622
75360
143509
143780
126728
277030
88316
324150
75441
139433
16802
66537
131183
10270
208754
5617
250821
291957
6732
20731
92838
41612
176596
286547
299815
220478
220624
312968
235113
260233
261355
10605
23346
15991
173121
38747
81445
69544
5082
193488

27471
74310
250284
38881
137141
5835
160606
194078
209951
157979
4201
8843
187808
191351
206074
208801
150429
177861
35219
41611
67084
10712
27968
69234
221848
75828
9663
1043
164655
315221
170472
157002
146228
36325
72799
154244
7278
129290
43801
6611
3000
12133
198630
130763
255635
258818
14034
136494
127650
36510
89931
80972
141725
1782
156007
246723
224590
218842
319792
22684
42057
191916
23920
125634
32828
14953
70597
18199
2391
3262
226426
17918
180916
19888
13416
57129
9603
39372
27546
3908
276817
236216
21555
29138
246568
13944
11585
34395
257851
15163
168687
9633
284417
11258
33875
225569
306637
209926
6574
4460
205072
19498
128425
162738
116860
1583
134637
170909
130908
15235
13403
17536
165748
120269
163399
194392
173504
174298
135840
102881
169366
131457
14452
13512
3053
2994
11437
10623
10964
10642
10641
12899
12897
13254
12071
12459
24078
23917
22377
25972
17895
19212
20889
21829
20772
5351
5635
5171
5698
5829
5826
4200
4959
4884
17397
11093
11038
11438
11436
10986
10579


314349
250463
92876
89404
88996
302914
259945
293207
313540
269623
56406
319114
324885
346482
118697
183346
25313
162191
318328
191880
256380
202223
200593
260348
135851
123514
203265
163481
15020
12920
253861
21702
5308
39342
46747
283848
231611
303621
303676
347146
319593
302840
292917
228889
188204
191879
287219
343898
289939
191081
300008
300007
205865
254227
246345
246203
241761
247643
243093
234977
318551
266129
270512
258544
263421
11208
11930
11968
9610
22801
22802
23684
22042
14383
14765
13576
17597
15855
15427
16158
2777
3390
663
1274
141042
141107
136285
148534
146290
119525
123495
130724
124378
129272
174927
176859
171411
171543
182172
182135
181089
183881
180340
157675
159865
165711
168457
167552
165208
32337
39636
39070
38678
26157
24901
25248
29939
28176
29107
29419
28650
88881
86587
84514
102750
100278
100670
105123
93402
55828
57422
43080
64570
66245
306680
260789
46745
72083
142333
156062
310953
313841
306169
287586
234101
340455
17457
150033
120801
110598
89611
86768

143070
217538
84609
242191
251208
83453
202624
136029
10780
343526
129603
188758
80869
173408
264714
11899
28989
312965
31216
187347
189610
237638
245528
234316
196953
237106
146259
32224
28257
169328
106969
10996
247526
105280
62374
284617
19834
21528
63015
10230
8514
18885
152955
235293
243940
292333
293274
9849
33625
27665
8448
140995
24125
29380
12130
15088
73230
4933
12519
151446
1343
6534
256964
281257
251661
244268
151985
108100
28861
222424
209322
165046
10171
107056
98931
51367
189919
207335
172118
182540
15791
7981
150978
39778
42498
189030
12532
8531
10203
36687
39447
26687
103807
204407
210935
99227
50444
31477
178038
235470
824
194438
286706
236881
28860
3524
7631
5211
5377
94073
256621
235513
148211
160762
224986
311465
19447
14991
40376
35482
7868
5026
36944
67712
69233
305865
303552
295221
300081
209853
23913
17348
3423
6675
150162
110434
170867
183364
157973
33569
39087
26635
37224
37168
287228
197788
140729
253819
266308
326908
289397
35896
237311
154006
152824
9988
2

In [29]:
# save catalog to file
#with open('data_cleaned/item_similarities_real_full.json', 'w') as convert_file:
#     convert_file.write(json.dumps(cleaned_storage))

In [9]:
# save catalog to file
#with open('data_cleaned/item_similarities_synth250_over750only.json', 'w') as convert_file:
#     convert_file.write(json.dumps(cleaned_storage))

In [2]:
# Opening JSON file
with open('data_cleaned/item_similarities_real_full.json') as json_file:
    item_similarities_real_full = json.load(json_file)

In [3]:
item_similarities_real_full['1']

{'213788': 0.22466644644737244,
 '206593': 0.22926782071590424,
 '267333': -0.04383024945855141,
 '301085': -0.9083207249641418,
 '261321': 0.282283216714859,
 '264212': -0.09897066652774811,
 '249552': 0.26086121797561646,
 '290618': 0.36738675832748413,
 '302933': 0.08364629745483398,
 '303734': -0.4036569893360138,
 '302510': 0.02065470814704895,
 '281094': -0.33643338084220886,
 '280281': -0.7513054609298706,
 '271064': 0.06866838037967682,
 '231309': 0.3220541477203369,
 '227212': 0.5692542195320129,
 '319999': -0.061500854790210724,
 '226085': 0.07338494062423706,
 '290722': 0.18054240942001343,
 '240423': 0.38079434633255005,
 '241203': 0.4567139446735382,
 '328569': -0.6498211026191711,
 '272767': -0.5513620376586914,
 '36218': 0.23173555731773376,
 '133473': -0.02531827986240387,
 '167791': 0.40416181087493896,
 '230802': 0.33140087127685547,
 '174430': 0.3610050082206726,
 '70919': -0.0383635088801384,
 '40834': 0.2542249858379364,
 '463': 0.12352059781551361,
 '181304': 0.09

In [4]:
pd.DataFrame.from_dict(item_similarities_real_full).head()

213788  206593    267333    249824    301085    261321    264212  \
261321  0.254606     NaN -0.736586       NaN -0.917090       NaN       NaN   
249552  0.363943     NaN       NaN       NaN -0.907534  0.874646       NaN   
302510 -0.782776     NaN -0.263589       NaN -0.646123  0.791039  0.394359   
271064  0.918197     NaN       NaN       NaN       NaN  0.596388       NaN   
287839  0.031220     NaN       NaN  0.794191       NaN       NaN       NaN   

          249552    290618    302933    303734    302510  281094    280281  \
261321  0.874646  0.980046 -0.588589 -0.898603  0.791039     NaN       NaN   
249552       NaN  0.916214 -0.525147 -0.823766  0.763460     NaN -0.546678   
302510  0.763460  0.175488  0.133239 -0.547952       NaN     NaN -0.561712   
271064  0.662601  0.727226  0.022670       NaN       NaN     NaN       NaN   
287839       NaN       NaN       NaN       NaN -0.096057     NaN       NaN   

          271064  240096  239808  232944    231309    227212    192696  \
261321  0.596388     NaN     NaN     NaN       NaN  0.495975       NaN   
249552  0.662601     NaN     NaN     NaN  0.378808  0.649346 -0.668178   
302510       NaN     NaN     NaN     NaN       NaN       NaN       NaN   
271064  1.000000     NaN     NaN     NaN -0.639149 -0.056588       NaN   
287839       NaN     NaN     NaN     NaN       NaN       NaN       NaN   

          319999    304434  232250    226085  230885  286885    290722  \
261321       NaN       NaN     NaN  0.195680     NaN     NaN  0.065858   
249552       NaN       NaN     NaN       NaN     NaN     NaN  0.048488   
302510  0.442308       NaN     NaN -0.363007     NaN     NaN  0.293376   
271064       NaN       NaN     NaN       NaN     NaN     NaN       NaN   
287839       NaN  0.492839     NaN       NaN     NaN     NaN       NaN   

          287839  317313    240423  252323  209667    241203    328569  \
261321       NaN     NaN -0.769324     NaN     NaN  0.727926       NaN   
249552       NaN     NaN -0.817061     NaN     NaN  0.826411       NaN   
302510 -0.096057     NaN       NaN     NaN     NaN       NaN  0.802078   
271064       NaN     NaN -0.838018     NaN     NaN  0.797688       NaN   
287839       NaN     NaN       NaN     NaN     NaN       NaN       NaN   

        248695  266079    272767  274152  258775  312613  311751    261588  \
261321     NaN     NaN       NaN     NaN     NaN     NaN     NaN  0.918050   
249552     NaN     NaN       NaN     NaN     NaN     NaN     NaN  0.908275   
302510     NaN     NaN -0.494908     NaN     NaN     NaN     NaN       NaN   
271064     NaN     NaN       NaN     NaN     NaN     NaN     NaN  0.741892   
287839     NaN     NaN  0.046512     NaN     NaN     NaN     NaN       NaN   

        261246     36218    133473    167791    230802    174430     70919  \
261321     NaN  0.214893 -0.194583  0.543225  0.285226  0.508778  0.258335   
249552     NaN  0.257223 -0.114042  0.560611  0.383786  0.492612  0.315483   
302510     NaN  0.128576 -0.166744 -0.020368  0.068004  0.223498  0.149255   
271064     NaN  0.284215 -0.137788  0.358397  0.206559  0.325064  0.093591   
287839     NaN -0.069383  0.031984 -0.478711 -0.272793 -0.173230 -0.157517   

           40834       463    181304    163412    170216    199561     70323  \
261321  0.140740  0.302727 -0.045665  0.072198  0.340431  0.233784  0.104285   
249552  0.322906  0.178659  0.068600  0.287780  0.429844  0.267095  0.024285   
302510  0.239935  0.053334  0.063819  0.088939  0.368265  0.290796  0.047029   
271064  0.300050  0.277279  0.076747  0.202632  0.226216  0.156351  0.048218   
287839  0.024474  0.190076 -0.359597  0.115521 -0.659284 -0.477305  0.089946   

          155426    147020    266192    160477    100423    205896     10547  \
261321  0.519845  0.417412  0.573995  0.415530  0.158949  0.253685 -0.085390   
249552  0.229370  0.456489  0.547663  0.229337  0.111813  0.229550 -0.023505   
302510  0.057160  0.094214  0.216105  0.244577 -0.120505  0.216697  0.212656  